# Q2_radiation_accessibility

In [1]:
import requests
import json
import pandas as pd
import geopandas as gpd
from pandas.core.frame import DataFrame
import os
import statistics as st
from osgeo import ogr
from shapely.geometry import MultiPolygon
from datetime import datetime
import pytz

In [2]:
#origin point csv
office=pd.read_csv('data/building.csv')
factory=pd.read_csv('data/industry.csv')
farm=pd.read_csv('data/farm.csv')
resident=gpd.read_file('data/centroids.shp')

#destination point csv
hospital=pd.read_csv('data/hospital.csv')
park=pd.read_csv('data/park.csv')
shop=pd.read_csv('data/shop.csv')

#supporting documents
township_list=pd.read_csv('data/Town_district_list.csv')

## Processing the Centroids shp to csv

In [3]:
resident=resident.to_crs("EPSG:4326")

In [4]:
resident.to_csv('data/resident.csv')

In [5]:
resident=pd.read_csv('data/resident.csv')

In [6]:
resident

Unnamed: 0  OBJECTID  Name Layer                   gml_id          code  \
0            0         1  沙河街道    乡镇                      NaN           NaN   
1            1         2  粤海街道    乡镇                      NaN           NaN   
2            2        13  凤凰街道    乡镇  layer_township_pg.15697  4.403110e+11   
3            3        14  玉塘街道    乡镇  layer_township_pg.15698  4.403110e+11   
4            4        15  光明街道    乡镇  layer_township_pg.15699  4.403110e+11   
..         ...       ...   ...   ...                      ...           ...   
69          69        88  大鹏街道    乡镇  layer_township_pg.15773  4.403070e+11   
70          70        19  南山街道    乡镇  layer_township_pg.15704  4.403050e+11   
71          71        48  海山街道    乡镇  layer_township_pg.15733  4.403080e+11   
72          72        43  盐田街道    乡镇  layer_township_pg.15728  4.403080e+11   
73          73        30  坑梓街道    乡镇  layer_township_pg.15715  4.403100e+11   

    grade    Shape_Leng    Shape_Area  \
0       0  20040.978853  2.179247e+07   
1       0  19159.589736  1.807562e+07   
2       4  29736.850664  2.598523e+07   
3       4  29501.182969  2.532503e+07   
4       4  30030.513705  3.424578e+07   
..    ...           ...           ...   
69      4  63412.662042  8.879811e+07   
70      4  33035.172793  3.875446e+07   
71      4  12242.843502  8.851195e+06   
72      4  32169.232404  5.358986e+07   
73      4  30569.061629  6.264222e+07   

                                       geometry  
0   POINT (113.9717641239288 22.53587233948723)  
1    POINT (113.9392492352695 22.5302223288828)  
2   POINT (113.9302728066271 22.73682204640801)  
3   POINT (113.8961826861495 22.71762848830217)  
4   POINT (113.9618129279743 22.75200408670002)  
..                                          ...  
69  POINT (114.5036482850048 22.60199187379314)  
70  POINT (113.8911273584019 22.51356938009944)  
71  POINT (114.2298682927088 22.56426415049962)  
72  POINT (114.2610436796775 22.60266935201232)  
73   POINT (114.384689538151 22.72313449498843)  

[74 rows x 10 columns]

In [7]:
resident[['point','cood']]=resident['geometry'].str.split('(', expand=True)
resident[['lng','lat']]=resident['cood'].str.split(' ', expand=True)
resident[['lat','no']]=resident['lat'].str.split(')', expand=True)
resident = resident[['Name','lat','lng']].copy()
resident=resident.rename(columns = {'Name':'name'})
resident

name                lat                lng
0   沙河街道  22.53587233948723  113.9717641239288
1   粤海街道   22.5302223288828  113.9392492352695
2   凤凰街道  22.73682204640801  113.9302728066271
3   玉塘街道  22.71762848830217  113.8961826861495
4   光明街道  22.75200408670002  113.9618129279743
..   ...                ...                ...
69  大鹏街道  22.60199187379314  114.5036482850048
70  南山街道  22.51356938009944  113.8911273584019
71  海山街道  22.56426415049962  114.2298682927088
72  盐田街道  22.60266935201232  114.2610436796775
73  坑梓街道  22.72313449498843   114.384689538151

[74 rows x 3 columns]

In [8]:
resident_new=resident.merge(township_list, how='inner', on='name')
resident_new['lat']=resident_new['lat'].apply(lambda x: float(x)).round(6)
resident_new['lng']=resident_new['lng'].apply(lambda x: float(x)).round(6)
resident_new

name        lat         lng district house_price_level
0   沙河街道  22.535872  113.971764       南山              high
1   粤海街道  22.530222  113.939249       南山              high
2   凤凰街道  22.736822  113.930273       光明            medium
3   玉塘街道  22.717628  113.896183       光明            medium
4   光明街道  22.752004  113.961813       光明            medium
..   ...        ...         ...      ...               ...
69  大鹏街道  22.601992  114.503648       大鹏               low
70  南山街道  22.513569  113.891127       南山              high
71  海山街道  22.564264  114.229868       盐田            medium
72  盐田街道  22.602669  114.261044       盐田            medium
73  坑梓街道  22.723134  114.384690       坪山               low

[74 rows x 5 columns]

In [9]:
resident_high=resident_new[resident_new['house_price_level']=='high'].reset_index(drop=True)
resident_medium=resident_new[resident_new['house_price_level']=='medium'].reset_index(drop=True)
resident_low=resident_new[resident_new['house_price_level']=='low'].reset_index(drop=True)

In [10]:
# Set for later document save
office.attrs['name'] = "office" 
factory.attrs['name'] = "factory" 
farm.attrs['name'] = "farm" 
resident_high.attrs['name'] = "resident_high" 
resident_medium.attrs['name'] = "resident_medium" 
resident_low.attrs['name'] = "resident_low"

hospital.attrs['name'] = "hospital" 
park.attrs['name'] = "park" 
shop.attrs['name'] = "shop" 

## Defining the functions

In [18]:
#Input: start latitude, start longitude, end latitude, end longitude
def stod(slat,slng,dlat,dlng):
    url ="http://api.map.baidu.com/direction/v2/transit?" #API address
    
    ak = 'xnrnvAZtT68KPGaw5MRcHkhMPlf8hAFi' #API key
    #ak = 'cGCdY6KHFma1t35LhDUZ13WI5qG1ni24' # second API key
    #ak = 'WdzbAKBkAombHOV93PjyjR2PihnGGGNQ' # third API key
    #ak= 'nt0YLRVb5Z7emBrqYTKcpHyMosFTsEGX' # forth API key
    
    #tac_metro = r'&tactics_incity=5' #Route planning with metro as the priority mode of travel
    real_url = url +"origin="+slat+","+slng+"&destination="+dlat+","+dlng+"&ak="+ak 
    req = requests.get(real_url)
    t = req.text
    data = json.loads(t) #save the data in the array data
    try: #Prevent some data errors from causing the request to terminate
        total_duration = data['result']["routes"][0]["duration"]/60
        #Get the total travel time of this piece of data
        stepstr = "Total time:"+str(total_duration) 
        #Get all steps of this roate
        steps = data['result']["routes"][0]['steps'] 
        for step in steps:
            # Introduction of each step including its mode of transportation
            step_tructions = step[0]["instructions"]
            # time spent in each step
            step_duration = step[0]["duration"]
            # Set a delimiter for the result for subsequent processing
            stepstr = stepstr+"/"+step_tructions+":"+str(step_duration/60)
    except:
        stepstr = None
    req.close()
    # The return data is the total duration/first step/first step time/second step/second step time/...
    return stepstr

In [12]:
# Sets the function that computes the average of the list for later use.
def ave(lst):
    try:
        if len(lst)==0:
            return 'None'
        elif len(lst)>0:
            return sum(lst) / len(lst)
        else:
            return 'None'
    except:
        return 'None'

In [13]:
def minx(lst):
    try:
        return min(lst)
    except:
        return "None"

In [14]:
def medianx(lst):
    try:
        return st.median(lst)
    except:
        return "None"

In [15]:
# Set up a function sor automatic loops, calculations and exported

def stodabc(csv_o,csv_d):
    
    # Get the local time and date when data collection started
    start_time = datetime.now(pytz.timezone('Asia/Shanghai'))
    st_string = start_time.strftime("%d/%m/%Y %H:%M:%S")
    
    #Set some empty lists for later use
    only_bus=[]
    only_walk=[]
    wrong_data=[]
    metro=[]
    walk=[]
    other=[]
    traffic=[]
    waiting=[]
    total=[]
    transfer=[]
    
    metro_min=[]
    metro_traffic_min=[]
    metro_transfer_min=[]
    
    traffic_min=[]
    traffic_metro_min=[]
    traffic_transfer_min=[]
    
    metro_median=[]
    traffic_median=[]
    transfer_median=[]

    # For all "starting data" in csv
    for o in range (len(csv_o['lat'])):
        
        print(csv_o['name'][o])

        d_metro_time_total=[]
        d_walk_time_total=[]
        d_other_time_total=[]
        d_total_time=[]
        d_waiting_time=[]
        d_status=[]
        d_transfer=[]
        d_traffic_time=[]

        # For all endpoint data in csv
        for d in range(len(csv_d['lat'])):
            s=str(stod(str(csv_o['lat'][o]),str(csv_o['lng'][o]),str(csv_d['lat'][d]),str(csv_d['lng'][d])))

            # From a starting point to each destination, if there is no line to reach the destination by metro:
            if s.find('乘地铁')==-1:
                
                # #Only accessible by bus
                if s.find('乘')!=-1:
                    result='Only bus can arrive'
                    i_walk_time_total=-10000
                    i_other_time_total=10000

                # #If it can only be reached by foot
                elif s.find('乘')==-1 and s.find('步行')!=-1:
                    result='Within walking distance'
                    i_walk_time_total=10000
                    i_other_time_total=-10000

                # #Unreachable case
                else:
                    result='Wrong cause without walking data, bus data or metro data'
                    i_walk_time_total=0
                    i_other_time_total=0
                i_metro_time_total=0
                i_total_time=0
                i_waiting_time=0
                i_transfer=-10000
                i_traffic_time=0

            # For the case where there is a route to the destination by metro
            elif s.find('乘地铁')!=-1:
                result='Can be arrived by metro'
                ## Calculate the number of transfers
                i_transfer=s.count('站内换乘')
                
                ##Process the data from the starting point to one of the ending points into a table
                first_split = s.split("/")
                dic= {'step':first_split}
                table = DataFrame(dic)
                table[['step','time']] = table['step'].str.split(':', expand=True)
                # table['time'] = table['time'].fillna(0)

                # # Extract data from the above table
                i_metro_time=[]
                i_walk_time=[]
                i_other_time=[]
                for i in range(len(table)):
                    # Extract metro ride time
                    if table['step'][i].find('乘地铁')!=-1 or table['step'][i].find('站内换乘')!=-1:
                        i_metro_time.append(float(table['time'][i]))
                    # Extract walking time
                    elif table['step'][i].find('乘地铁')==-1 and table['step'][i].find('步行')!=-1 and table['step'][i].find('站内换乘')==-1:
                        i_walk_time.append(float(table['time'][i]))
                    # Extract the whole time (including waiting time)
                    elif table['step'][i].find('Total time')!=-1:
                        i_total_time=float(table['time'][i])
                    # Extract the time of other means of transportation
                    else:
                        i_other_time.append(float(table['time'][i]))

                # Calculate the total time of each type of time
                i_metro_time_total=sum(i_metro_time)
                i_walk_time_total=sum(i_walk_time)
                i_other_time_total=sum(i_other_time)
                # #Extract time spent using transportation and walking
                i_traffic_time=i_metro_time_total+i_walk_time_total+i_other_time_total
                #Calculate the waiting time
                i_waiting_time=i_total_time-i_traffic_time

            # # Handling other error data
            else:
                result='Wrong cause contradict result'
                i_metro_time_total=404
                i_walk_time_total=404
                i_other_time_total=404
                i_total_time=404
                i_waiting_time=404
                i_transfer=404
                i_traffic_time=404

            # #Package all the above data from the starting point to each end point
            d_metro_time_total.append(i_metro_time_total)
            d_walk_time_total.append(i_walk_time_total)
            d_other_time_total.append(i_other_time_total)
            d_total_time.append(i_total_time)
            d_waiting_time.append(i_waiting_time)
            d_status.append(result)
            d_transfer.append(i_transfer)
            d_traffic_time.append(i_traffic_time)
            print(csv_d['name'][d])

        d_dic={'Destination':csv_d['name'],
               'Status':d_status,
               'Metro_time':d_metro_time_total,
               'Walk_time':d_walk_time_total,
               'Other_time':d_other_time_total,
               'Traffic_time':d_traffic_time,
               'Waiting_time':d_waiting_time,
               'Total_time':d_total_time,
               'Transfer':d_transfer}
        d_final=DataFrame(d_dic)

        # #Consider the processing of different result data
        f_only_bus=[]
        f_only_walk=[]
        f_wrong_data=[]
        f_metro=[]
        f_walk=[]
        f_other=[]
        f_traffic=[]
        f_waiting=[]
        f_total=[]
        f_transfer=[]
        for f in range (len(d_final['Destination'])):
            if d_final['Status'][f]=='Only bus can arrive':
                f_only_bus.append(d_final['Other_time'][f])
            elif d_final['Status'][f]=='Within walking distance':
                f_only_walk.append(d_final['Walk_time'][f])
            elif d_final['Status'][f]=='Can be arrived by metro':
                f_metro.append(d_final['Metro_time'][f])
                f_walk.append(d_final['Walk_time'][f])
                f_other.append(d_final['Other_time'][f])
                f_traffic.append(d_final['Traffic_time'][f])
                f_waiting.append(d_final['Waiting_time'][f])
                f_total.append(d_final['Total_time'][f])
                f_transfer.append(d_final['Transfer'][f])
            else:
                f_wrong_data.append(d_final['Transfer'][f])

        # Calculate the average from one starting point to all ending points, 
        # and pack it into a list of all starting point results
        only_bus.append(len(f_only_bus))
        only_walk.append(len(f_only_walk))
        wrong_data.append(len(f_wrong_data))
        metro.append(ave(f_metro))
        walk.append(ave(f_walk))
        other.append(ave(f_other))
        traffic.append(ave(f_traffic))
        waiting.append(ave(f_waiting))
        total.append(ave(f_total))
        transfer.append(ave(f_transfer))
        
        # Calculate the shortest metro rade time from one starting point to all ending points, etc.,
        # and pack it into a list of all starting point results
        metro_min.append(minx(f_metro))
        if minx(f_metro)!='None':
            metro_traffic_min.append(f_traffic[f_metro.index(min(f_metro))])
            metro_transfer_min.append(f_transfer[f_metro.index(min(f_metro))])
        else:
            metro_traffic_min.append('None')
            metro_transfer_min.append('None')
        
        # Calculate the shortest traffic time from one starting point to all ending points, etc.,
        # and pack it into a list of all starting point results
        traffic_min.append(minx(f_traffic))
        if minx(f_traffic)!='None':
            traffic_metro_min.append(f_metro[f_traffic.index(min(f_traffic))])
            traffic_transfer_min.append(f_transfer[f_traffic.index(min(f_traffic))])
        else:
            traffic_metro_min.append('None')
            traffic_transfer_min.append('None')
        
        # Calculate the median from one starting point to all ending points, 
        # and pack it into a list of all starting point results
        metro_median.append(medianx(f_metro))
        if medianx(f_metro)!='None':
            traffic_median.append(st.median(f_traffic))
            transfer_median.append(st.median(f_transfer))
        else:
            traffic_median.append('None')
            transfer_median.append('None')
        
        #Print recent data to visit progress as it runs
        print(str(only_bus)+","+str(only_walk)+","+str(wrong_data)+","+str(metro)+","+str(walk)+","+str(other)+","+str(traffic)+","+str(waiting)+","+str(total)+","+str(transfer)+
             str(metro_min)+","+str(metro_traffic_min)+","+str(metro_transfer_min)+","+
             str(traffic_min)+","+str(traffic_metro_min)+","+str(traffic_transfer_min)+","+
             str(metro_median)+","+str(traffic_median)+","+str(transfer_median))

    # Make the result into a dataframe
    dic={'Origin':csv_o['name'],
         'Average_metro_time':metro,
         'Average_walk_time':walk,
         'Average_other_time':other,
         'Average_traffic_time':traffic,
         'Average_waiting_time':waiting,
         'Average_total_time':total,
         'Average_metro_line_transfer':transfer,
         'Min_metro_time':metro_min,
         'Traffic_time_of min_metro_time':metro_traffic_min,
         'Transfer_of_min_metro_time':metro_transfer_min,
         'Min_traffic_time':traffic_min,
         'Metro_time_of_min_traffic_time':traffic_metro_min,
         'Transfer_of_min_traffic_time':traffic_transfer_min,
         'Median_metro_time':metro_median,
         'Median_traffic_time':traffic_median,
         'Median_metro_line_transfer':transfer_median,
        'Count_of_only_bus_round':only_bus,
        'Count_of only_walk_round':only_walk,
        'Count_of_none_data':wrong_data}
    
    final=DataFrame(dic)
    print(final)
    
    # Get the local time and date when data collection ended
    end_time = datetime.now(pytz.timezone('Asia/Shanghai'))
    et_string = end_time.strftime("%d/%m/%Y %H:%M:%S")
    
    # Print started and ended time
    print("The start time of collection in China is : ")
    print(st_string)
    print('The end time of collection in China is : ')
    print(et_string)
    
    # save dataframe to folder as a csv
    final.to_csv('output_data/'+csv_o.attrs['name']+'_to_'+ csv_d.attrs['name']+'.csv')

# Get data

In [34]:
#Because the daily quota limitation of API, results cannot be obtained in one time. 
#The following code have been abandoned.
'''
origin=[farm,factory,office,resident_low,resident_high,resident_medium]
destination=[hospital,shop,park]

for o_file in origin:
    for d_file in destination:
        stodabc(o_file,d_file)
'''


'\norigin=[farm,factory,office,resident_low,resident_high,resident_medium]\ndestination=[hospital,shop,park]\n\nfor o_file in origin:\n    for d_file in destination:\n        stodabc(o_file,d_file)\n'

In [36]:
stodabc(farm,shop)

鹏飞路310号
华润万家(龙华店)
华润万家(益田店)
华润万家(沙井店)
华润万家(横岗店)
华润万家(宝安店)
华润万家(侨香店)
华润万家(春风店)
华润万家(莲塘店)
华润万家(西丽店)
华润万家(深盐店)
华润万家(世贸百货店)-停车场
华润万家(喜港城店)-正门
华润万家(下水径店)
华润万家(民乐店)
华润万家(福星店)
华润万家(翠竹店)
华润万家(龙城店)
深圳华润万家欢乐颂店2楼曼妮芬
华润万家(宝安中心店)
华润万家(银湖店)
来电(华润万家布吉百鸽笼店)
华润万家(莲花北店)
华润万家(天安云谷店)
华润万家(深汕路店)
华润万家(梅林一村店)
华润万家(红岭店)
华润万家(宏发领域店)
华润万家(深圳龙岗天安数码店)
华润万家(南湾店)
华润万家(大唐时代分店)
华润万家(梅陇镇店)
华润万家(吉祥路店)
华润万家(深南大道店)
华润万家(欢乐海岸店)
华润万家(摩尔城店)
华润万家(四季花城3分店)
华润万家(松坪山店)
华润万家(吉莲店)
华润万家(方鼎店)
华润万家(新时代店)
华润万家(沙园路店)
华润万家(宏发君域店)
华润万家(龙园店)
华润万家(李朗国际珠宝产业园店)
华润万家(美莲店)
华润万家(海源城一分店)
华润万家(深圳黄金大厦店)
华润万家(碧华店)
华润万家(南方店)
华润万家(宝安店)-正门
华润万家(凤凰店)
华润万家(赤湾六路店)
华润万家(新闻路店)
华润万家(桂芳园二店)
华润万家(中海怡翠店)
华润万家(慢城店)
华润万家(登良路店)
华润万家(东方沁园店)
华润万家(华清园店)
华润万家(水山缘店)
华润万家(麓园店)
[34],[0],[0],[31.56481481481481],[28.59567901234568],[104.28271604938271],[164.44320987654322],[25.73333333333333],[190.17654320987654],[0.25925925925925924][8.0],[131.66666666666669],[0],[119.13333333333334],[10.0],[0],[24.0],[169.9],[0]
双晖现代农业
华润万家(龙华店)
华润万家(益田店)
华润万家(沙井店)
华润万家(横岗店)
华润万家(宝安店)


In [19]:
stodabc(resident_high,shop)

沙河街道
华润万家(龙华店)
华润万家(益田店)
华润万家(沙井店)
华润万家(横岗店)
华润万家(宝安店)
华润万家(侨香店)
华润万家(春风店)
华润万家(莲塘店)
华润万家(西丽店)
华润万家(深盐店)
华润万家(世贸百货店)-停车场
华润万家(喜港城店)-正门
华润万家(下水径店)
华润万家(民乐店)
华润万家(福星店)
华润万家(翠竹店)
华润万家(龙城店)
深圳华润万家欢乐颂店2楼曼妮芬
华润万家(宝安中心店)
华润万家(银湖店)
来电(华润万家布吉百鸽笼店)
华润万家(莲花北店)
华润万家(天安云谷店)
华润万家(深汕路店)
华润万家(梅林一村店)
华润万家(红岭店)
华润万家(宏发领域店)
华润万家(深圳龙岗天安数码店)
华润万家(南湾店)
华润万家(大唐时代分店)
华润万家(梅陇镇店)
华润万家(吉祥路店)
华润万家(深南大道店)
华润万家(欢乐海岸店)
华润万家(摩尔城店)
华润万家(四季花城3分店)
华润万家(松坪山店)
华润万家(吉莲店)
华润万家(方鼎店)
华润万家(新时代店)
华润万家(沙园路店)
华润万家(宏发君域店)
华润万家(龙园店)
华润万家(李朗国际珠宝产业园店)
华润万家(美莲店)
华润万家(海源城一分店)
华润万家(深圳黄金大厦店)
华润万家(碧华店)
华润万家(南方店)
华润万家(宝安店)-正门
华润万家(凤凰店)
华润万家(赤湾六路店)
华润万家(新闻路店)
华润万家(桂芳园二店)
华润万家(中海怡翠店)
华润万家(慢城店)
华润万家(登良路店)
华润万家(东方沁园店)
华润万家(华清园店)
华润万家(水山缘店)
华润万家(麓园店)
[27],[0],[0],[40.93480392156863],[23.082352941176467],[6.449509803921569],[70.46666666666667],[7.279411764705884],[77.74607843137257],[0.6764705882352942][5.0],[31.0],[0],[30.96666666666667],[9.0],[0],[42.233333333333334],[68.825],[1.0]
粤海街道
华润万家(龙华店)
华润万家(益田店)
华润万家(沙井店)
华润万家(横岗店)
华润万家(宝安店)
华润万家(侨香

In [21]:
stodabc(resident_medium,shop)

凤凰街道
华润万家(龙华店)
华润万家(益田店)
华润万家(沙井店)
华润万家(横岗店)
华润万家(宝安店)
华润万家(侨香店)
华润万家(春风店)
华润万家(莲塘店)
华润万家(西丽店)
华润万家(深盐店)
华润万家(世贸百货店)-停车场
华润万家(喜港城店)-正门
华润万家(下水径店)
华润万家(民乐店)
华润万家(福星店)
华润万家(翠竹店)
华润万家(龙城店)
深圳华润万家欢乐颂店2楼曼妮芬
华润万家(宝安中心店)
华润万家(银湖店)
来电(华润万家布吉百鸽笼店)
华润万家(莲花北店)
华润万家(天安云谷店)
华润万家(深汕路店)
华润万家(梅林一村店)
华润万家(红岭店)
华润万家(宏发领域店)
华润万家(深圳龙岗天安数码店)
华润万家(南湾店)
华润万家(大唐时代分店)
华润万家(梅陇镇店)
华润万家(吉祥路店)
华润万家(深南大道店)
华润万家(欢乐海岸店)
华润万家(摩尔城店)
华润万家(四季花城3分店)
华润万家(松坪山店)
华润万家(吉莲店)
华润万家(方鼎店)
华润万家(新时代店)
华润万家(沙园路店)
华润万家(宏发君域店)
华润万家(龙园店)
华润万家(李朗国际珠宝产业园店)
华润万家(美莲店)
华润万家(海源城一分店)
华润万家(深圳黄金大厦店)
华润万家(碧华店)
华润万家(南方店)
华润万家(宝安店)-正门
华润万家(凤凰店)
华润万家(赤湾六路店)
华润万家(新闻路店)
华润万家(桂芳园二店)
华润万家(中海怡翠店)
华润万家(慢城店)
华润万家(登良路店)
华润万家(东方沁园店)
华润万家(华清园店)
华润万家(水山缘店)
华润万家(麓园店)
[14],[0],[0],[46.146453900709226],[22.629787234042553],[9.506028368794324],[78.2822695035461],[15.212765957446809],[93.49503546099291],[1.2553191489361701][17.0],[55.983333333333334],[0],[51.0],[29.15],[1],[43.15],[75.83333333333333],[1]
玉塘街道
华润万家(龙华店)
华润万家(益田店)
华润万家(沙井店)
华润万家(横岗店)
华润万家(宝安店)
华润万家(侨

In [16]:
stodabc(resident_low,shop)

坪山街道
华润万家(龙华店)
华润万家(益田店)
华润万家(沙井店)
华润万家(横岗店)
华润万家(宝安店)
华润万家(侨香店)
华润万家(春风店)
华润万家(莲塘店)
华润万家(西丽店)
华润万家(深盐店)
华润万家(世贸百货店)-停车场
华润万家(喜港城店)-正门
华润万家(下水径店)
华润万家(民乐店)
华润万家(福星店)
华润万家(翠竹店)
华润万家(龙城店)
深圳华润万家欢乐颂店2楼曼妮芬
华润万家(宝安中心店)
华润万家(银湖店)
来电(华润万家布吉百鸽笼店)
华润万家(莲花北店)
华润万家(天安云谷店)
华润万家(深汕路店)
华润万家(梅林一村店)
华润万家(红岭店)
华润万家(宏发领域店)
华润万家(深圳龙岗天安数码店)
华润万家(南湾店)
华润万家(大唐时代分店)
华润万家(梅陇镇店)
华润万家(吉祥路店)
华润万家(深南大道店)
华润万家(欢乐海岸店)
华润万家(摩尔城店)
华润万家(四季花城3分店)
华润万家(松坪山店)
华润万家(吉莲店)
华润万家(方鼎店)
华润万家(新时代店)
华润万家(沙园路店)
华润万家(宏发君域店)
华润万家(龙园店)
华润万家(李朗国际珠宝产业园店)
华润万家(美莲店)
华润万家(海源城一分店)
华润万家(深圳黄金大厦店)
华润万家(碧华店)
华润万家(南方店)
华润万家(宝安店)-正门
华润万家(凤凰店)
华润万家(赤湾六路店)
华润万家(新闻路店)
华润万家(桂芳园二店)
华润万家(中海怡翠店)
华润万家(慢城店)
华润万家(登良路店)
华润万家(东方沁园店)
华润万家(华清园店)
华润万家(水山缘店)
华润万家(麓园店)
[38],[0],[0],[62.44927536231885],[22.860869565217396],[37.04130434782609],[122.35144927536233],[16.195652173913043],[138.54710144927537],[0.9565217391304348][13.616666666666667],[70.28333333333333],[1],[70.28333333333333],[13.616666666666667],[1],[64.61666666666667],[123.5],[1]
石井街道
华润万家(龙华店)
华润万家(

In [18]:
stodabc(factory,shop)

华强创意产业园
华润万家(龙华店)
华润万家(益田店)
华润万家(沙井店)
华润万家(横岗店)
华润万家(宝安店)
华润万家(侨香店)
华润万家(春风店)
华润万家(莲塘店)
华润万家(西丽店)
华润万家(深盐店)
华润万家(世贸百货店)-停车场
华润万家(喜港城店)-正门
华润万家(下水径店)
华润万家(民乐店)
华润万家(福星店)
华润万家(翠竹店)
华润万家(龙城店)
深圳华润万家欢乐颂店2楼曼妮芬
华润万家(宝安中心店)
华润万家(银湖店)
来电(华润万家布吉百鸽笼店)
华润万家(莲花北店)
华润万家(天安云谷店)
华润万家(深汕路店)
华润万家(梅林一村店)
华润万家(红岭店)
华润万家(宏发领域店)
华润万家(深圳龙岗天安数码店)
华润万家(南湾店)
华润万家(大唐时代分店)
华润万家(梅陇镇店)
华润万家(吉祥路店)
华润万家(深南大道店)
华润万家(欢乐海岸店)
华润万家(摩尔城店)
华润万家(四季花城3分店)
华润万家(松坪山店)
华润万家(吉莲店)
华润万家(方鼎店)
华润万家(新时代店)
华润万家(沙园路店)
华润万家(宏发君域店)
华润万家(龙园店)
华润万家(李朗国际珠宝产业园店)
华润万家(美莲店)
华润万家(海源城一分店)
华润万家(深圳黄金大厦店)
华润万家(碧华店)
华润万家(南方店)
华润万家(宝安店)-正门
华润万家(凤凰店)
华润万家(赤湾六路店)
华润万家(新闻路店)
华润万家(桂芳园二店)
华润万家(中海怡翠店)
华润万家(慢城店)
华润万家(登良路店)
华润万家(东方沁园店)
华润万家(华清园店)
华润万家(水山缘店)
华润万家(麓园店)
[10],[0],[0],[47.64411764705884],[21.287908496732026],[32.03006535947712],[100.96209150326798],[18.872549019607842],[119.8346405228758],[1.2352941176470589][17.0],[114.21666666666668],[0],[60.63333333333334],[24.0],[0],[45.15],[102.76666666666667],[1]
深圳市生物医药创新产业园
华润万家(龙华店)
华润万家(益田店)
华润万家(沙井店)
华

In [16]:
stodabc(office,shop)

龙岗创投大厦
华润万家(龙华店)
华润万家(益田店)
华润万家(沙井店)
华润万家(横岗店)
华润万家(宝安店)
华润万家(侨香店)
华润万家(春风店)
华润万家(莲塘店)
华润万家(西丽店)
华润万家(深盐店)
华润万家(世贸百货店)-停车场
华润万家(喜港城店)-正门
华润万家(下水径店)
华润万家(民乐店)
华润万家(福星店)
华润万家(翠竹店)
华润万家(龙城店)
深圳华润万家欢乐颂店2楼曼妮芬
华润万家(宝安中心店)
华润万家(银湖店)
来电(华润万家布吉百鸽笼店)
华润万家(莲花北店)
华润万家(天安云谷店)
华润万家(深汕路店)
华润万家(梅林一村店)
华润万家(红岭店)
华润万家(宏发领域店)
华润万家(深圳龙岗天安数码店)
华润万家(南湾店)
华润万家(大唐时代分店)
华润万家(梅陇镇店)
华润万家(吉祥路店)
华润万家(深南大道店)
华润万家(欢乐海岸店)
华润万家(摩尔城店)
华润万家(四季花城3分店)
华润万家(松坪山店)
华润万家(吉莲店)
华润万家(方鼎店)
华润万家(新时代店)
华润万家(沙园路店)
华润万家(宏发君域店)
华润万家(龙园店)
华润万家(李朗国际珠宝产业园店)
华润万家(美莲店)
华润万家(海源城一分店)
华润万家(深圳黄金大厦店)
华润万家(碧华店)
华润万家(南方店)
华润万家(宝安店)-正门
华润万家(凤凰店)
华润万家(赤湾六路店)
华润万家(新闻路店)
华润万家(桂芳园二店)
华润万家(中海怡翠店)
华润万家(慢城店)
华润万家(登良路店)
华润万家(东方沁园店)
华润万家(华清园店)
华润万家(水山缘店)
华润万家(麓园店)
[37],[0],[1],[42.5304347826087],[20.56449275362319],[36.005072463768116],[99.1],[14.23913043478261],[113.3391304347826],[0.43478260869565216][8.0],[50.56666666666667],[0],[50.56666666666667],[8.0],[0],[32.0],[101.15],[0]
深圳国际文化大厦
华润万家(龙华店)
华润万家(益田店)
华润万家(沙井店)
华润万家(横岗店)
华润万家(宝安店)
华润万家(侨香店)
华润万家(春风

In [18]:
stodabc(office,hospital)

龙岗创投大厦
北京大学深圳医院
香港大学深圳医院
深圳市第二人民医院
深圳市中医院
中山大学附属第八医院
广州中医药大学深圳医院(福田)
深圳市福田区第二人民医院
深圳景田医院
深圳市人民医院
深圳市康宁医院(罗湖院区)
深圳市罗湖区人民医院
罗湖区中医院
深圳出入境边防检查总站医院
深圳市盐田区人民医院
深圳大学总医院
中国医学科学院阜外医院深圳医院
深圳市南山区人民医院
南方科技大学医院
南方医科大学深圳医院
深圳市宝安区人民医院
深圳市宝安第二人民医院(集团)总医院
深圳市龙岗区第三人民医院
宝安中医院(集团)
深圳市中西医结合医院
深圳市宝安区中心医院
宝安纯中医治疗医院
深圳恒生医院
深圳万丰医院
深圳市第三人民医院
深圳市龙岗中心医院
深圳市龙岗区人民医院
龙岗区第二人民医院
深圳市龙岗区第四人民医院
深圳市龙岗区第五人民医院
深圳市龙岗区第六人民医院
北京中医药大学深圳医院
深圳市龙岗区耳鼻咽喉医院
深圳龙城医院
深圳华侨医院
深圳肖传国医院
深圳市人民医院龙华分院
深圳市龙华区人民医院
深圳市龙华区中心医院
深圳军龙医院
深圳市康宁医院(坪山院区)
深圳市坪山区人民医院
中山大学附属第七医院
中国科学院大学深圳医院(东院区)
深圳市大鹏新区葵涌人民医院
深圳市大鹏新区南澳人民医院
[34],[0],[0],[49.94166666666666],[24.82291666666666],[35.40833333333333],[110.17291666666665],[16.250000000000004],[126.42291666666665],[0.5][4.0],[50.15],[0],[50.15],[4.0],[0],[46.5],[116.275],[0.5]
深圳国际文化大厦
北京大学深圳医院
香港大学深圳医院
深圳市第二人民医院
深圳市中医院
中山大学附属第八医院
广州中医药大学深圳医院(福田)
深圳市福田区第二人民医院
深圳景田医院
深圳市人民医院
深圳市康宁医院(罗湖院区)
深圳市罗湖区人民医院
罗湖区中医院
深圳出入境边防检查总站医院
深圳市盐田区人民医院
深圳大学总医院
中国医学科学院阜外医院深圳医院
深圳市南山区人民医院
南方科技大学医院
南方医科大学深圳医院
深圳市宝安区人民医院
深圳市宝安第二人民医院(集团)总医院
深圳

In [20]:
stodabc(factory,hospital)

华强创意产业园
北京大学深圳医院
香港大学深圳医院
深圳市第二人民医院
深圳市中医院
中山大学附属第八医院
广州中医药大学深圳医院(福田)
深圳市福田区第二人民医院
深圳景田医院
深圳市人民医院
深圳市康宁医院(罗湖院区)
深圳市罗湖区人民医院
罗湖区中医院
深圳出入境边防检查总站医院
深圳市盐田区人民医院
深圳大学总医院
中国医学科学院阜外医院深圳医院
深圳市南山区人民医院
南方科技大学医院
南方医科大学深圳医院
深圳市宝安区人民医院
深圳市宝安第二人民医院(集团)总医院
深圳市龙岗区第三人民医院
宝安中医院(集团)
深圳市中西医结合医院
深圳市宝安区中心医院
宝安纯中医治疗医院
深圳恒生医院
深圳万丰医院
深圳市第三人民医院
深圳市龙岗中心医院
深圳市龙岗区人民医院
龙岗区第二人民医院
深圳市龙岗区第四人民医院
深圳市龙岗区第五人民医院
深圳市龙岗区第六人民医院
北京中医药大学深圳医院
深圳市龙岗区耳鼻咽喉医院
深圳龙城医院
深圳华侨医院
深圳肖传国医院
深圳市人民医院龙华分院
深圳市龙华区人民医院
深圳市龙华区中心医院
深圳军龙医院
深圳市康宁医院(坪山院区)
深圳市坪山区人民医院
中山大学附属第七医院
中国科学院大学深圳医院(东院区)
深圳市大鹏新区葵涌人民医院
深圳市大鹏新区南澳人民医院
[16],[0],[0],[52.25392156862746],[22.733333333333334],[33.4656862745098],[108.45294117647056],[18.970588235294116],[127.42352941176469],[1.3235294117647058][30.15],[97.68333333333334],[1],[71.03333333333333],[41.15],[1],[48.13333333333333],[102.31666666666666],[1.0]
深圳市生物医药创新产业园
北京大学深圳医院
香港大学深圳医院
深圳市第二人民医院
深圳市中医院
中山大学附属第八医院
广州中医药大学深圳医院(福田)
深圳市福田区第二人民医院
深圳景田医院
深圳市人民医院
深圳市康宁医院(罗湖院区)
深圳市罗湖区人民医院
罗湖区中医院
深圳出入境边防检查总站医院
深圳市盐田区人民医院
深圳大学总医院
中国医学科学院

In [20]:
stodabc(farm,hospital)

鹏飞路310号
北京大学深圳医院
香港大学深圳医院
深圳市第二人民医院
深圳市中医院
中山大学附属第八医院
广州中医药大学深圳医院(福田)
深圳市福田区第二人民医院
深圳景田医院
深圳市人民医院
深圳市康宁医院(罗湖院区)
深圳市罗湖区人民医院
罗湖区中医院
深圳出入境边防检查总站医院
深圳市盐田区人民医院
深圳大学总医院
中国医学科学院阜外医院深圳医院
深圳市南山区人民医院
南方科技大学医院
南方医科大学深圳医院
深圳市宝安区人民医院
深圳市宝安第二人民医院(集团)总医院
深圳市龙岗区第三人民医院
宝安中医院(集团)
深圳市中西医结合医院
深圳市宝安区中心医院
宝安纯中医治疗医院
深圳恒生医院
深圳万丰医院
深圳市第三人民医院
深圳市龙岗中心医院
深圳市龙岗区人民医院
龙岗区第二人民医院
深圳市龙岗区第四人民医院
深圳市龙岗区第五人民医院
深圳市龙岗区第六人民医院
北京中医药大学深圳医院
深圳市龙岗区耳鼻咽喉医院
深圳龙城医院
深圳华侨医院
深圳肖传国医院
深圳市人民医院龙华分院
深圳市龙华区人民医院
深圳市龙华区中心医院
深圳军龙医院
深圳市康宁医院(坪山院区)
深圳市坪山区人民医院
中山大学附属第七医院
中国科学院大学深圳医院(东院区)
深圳市大鹏新区葵涌人民医院
深圳市大鹏新区南澳人民医院
[26],[0],[0],[32.97569444444444],[32.52847222222222],[97.02291666666667],[162.52708333333334],[26.770138888888894],[189.29722222222225],[0.375][4.0],[133.58333333333331],[0],[106.6],[14.233333333333333],[1],[29.191666666666666],[162.06666666666666],[0.0]
双晖现代农业
北京大学深圳医院
香港大学深圳医院
深圳市第二人民医院
深圳市中医院
中山大学附属第八医院
广州中医药大学深圳医院(福田)
深圳市福田区第二人民医院
深圳景田医院
深圳市人民医院
深圳市康宁医院(罗湖院区)
深圳市罗湖区人民医院
罗湖区中医院
深圳出入境边防检查总站医院
深圳市盐田区人民医院
深圳大学总医院
中国医学科学院阜外医院深圳医院
深圳市南山区人民医

In [22]:
stodabc(resident_low,hospital)

坪山街道
北京大学深圳医院
香港大学深圳医院
深圳市第二人民医院
深圳市中医院
中山大学附属第八医院
广州中医药大学深圳医院(福田)
深圳市福田区第二人民医院
深圳景田医院
深圳市人民医院
深圳市康宁医院(罗湖院区)
深圳市罗湖区人民医院
罗湖区中医院
深圳出入境边防检查总站医院
深圳市盐田区人民医院
深圳大学总医院
中国医学科学院阜外医院深圳医院
深圳市南山区人民医院
南方科技大学医院
南方医科大学深圳医院
深圳市宝安区人民医院
深圳市宝安第二人民医院(集团)总医院
深圳市龙岗区第三人民医院
宝安中医院(集团)
深圳市中西医结合医院
深圳市宝安区中心医院
宝安纯中医治疗医院
深圳恒生医院
深圳万丰医院
深圳市第三人民医院
深圳市龙岗中心医院
深圳市龙岗区人民医院
龙岗区第二人民医院
深圳市龙岗区第四人民医院
深圳市龙岗区第五人民医院
深圳市龙岗区第六人民医院
北京中医药大学深圳医院
深圳市龙岗区耳鼻咽喉医院
深圳龙城医院
深圳华侨医院
深圳肖传国医院
深圳市人民医院龙华分院
深圳市龙华区人民医院
深圳市龙华区中心医院
深圳军龙医院
深圳市康宁医院(坪山院区)
深圳市坪山区人民医院
中山大学附属第七医院
中国科学院大学深圳医院(东院区)
深圳市大鹏新区葵涌人民医院
深圳市大鹏新区南澳人民医院
[28],[0],[0],[62.86515151515152],[24.862121212121203],[38.293939393939404],[126.02121212121214],[17.727272727272723],[143.74848484848488],[1.0][3.0],[55.050000000000004],[0],[55.050000000000004],[3.0],[0],[60.25833333333333],[129.875],[1.0]
石井街道
北京大学深圳医院
香港大学深圳医院
深圳市第二人民医院
深圳市中医院
中山大学附属第八医院
广州中医药大学深圳医院(福田)
深圳市福田区第二人民医院
深圳景田医院
深圳市人民医院
深圳市康宁医院(罗湖院区)
深圳市罗湖区人民医院
罗湖区中医院
深圳出入境边防检查总站医院
深圳市盐田区人民医院
深圳大学总医院
中国医学科学院阜外医院深圳医院
深圳市南山区人民医院
南方科技大学医院
南方医科大学深圳

In [16]:
stodabc(resident_medium,hospital)

凤凰街道
北京大学深圳医院
香港大学深圳医院
深圳市第二人民医院
深圳市中医院
中山大学附属第八医院
广州中医药大学深圳医院(福田)
深圳市福田区第二人民医院
深圳景田医院
深圳市人民医院
深圳市康宁医院(罗湖院区)
深圳市罗湖区人民医院
罗湖区中医院
深圳出入境边防检查总站医院
深圳市盐田区人民医院
深圳大学总医院
中国医学科学院阜外医院深圳医院
深圳市南山区人民医院
南方科技大学医院
南方医科大学深圳医院
深圳市宝安区人民医院
深圳市宝安第二人民医院(集团)总医院
深圳市龙岗区第三人民医院
宝安中医院(集团)
深圳市中西医结合医院
深圳市宝安区中心医院
宝安纯中医治疗医院
深圳恒生医院
深圳万丰医院
深圳市第三人民医院
深圳市龙岗中心医院
深圳市龙岗区人民医院
龙岗区第二人民医院
深圳市龙岗区第四人民医院
深圳市龙岗区第五人民医院
深圳市龙岗区第六人民医院
北京中医药大学深圳医院
深圳市龙岗区耳鼻咽喉医院
深圳龙城医院
深圳华侨医院
深圳肖传国医院
深圳市人民医院龙华分院
深圳市龙华区人民医院
深圳市龙华区中心医院
深圳军龙医院
深圳市康宁医院(坪山院区)
深圳市坪山区人民医院
中山大学附属第七医院
中国科学院大学深圳医院(东院区)
深圳市大鹏新区葵涌人民医院
深圳市大鹏新区南澳人民医院
[8],[0],[0],[50.026587301587305],[21.509126984126983],[13.787301587301586],[85.3230158730159],[17.916666666666668],[103.23968253968253],[1.2142857142857142][12.0],[53.300000000000004],[0],[52.71666666666667],[12.0],[0],[47.625],[77.39166666666667],[1.0]
玉塘街道
北京大学深圳医院
香港大学深圳医院
深圳市第二人民医院
深圳市中医院
中山大学附属第八医院
广州中医药大学深圳医院(福田)
深圳市福田区第二人民医院
深圳景田医院
深圳市人民医院
深圳市康宁医院(罗湖院区)
深圳市罗湖区人民医院
罗湖区中医院
深圳出入境边防检查总站医院
深圳市盐田区人民医院
深圳大学总医院
中国医学科学院阜外医院深圳医院
深圳市南山区人民医院
南方科技

In [19]:
stodabc(resident_high,hospital)

沙河街道
北京大学深圳医院
香港大学深圳医院
深圳市第二人民医院
深圳市中医院
中山大学附属第八医院
广州中医药大学深圳医院(福田)
深圳市福田区第二人民医院
深圳景田医院
深圳市人民医院
深圳市康宁医院(罗湖院区)
深圳市罗湖区人民医院
罗湖区中医院
深圳出入境边防检查总站医院
深圳市盐田区人民医院
深圳大学总医院
中国医学科学院阜外医院深圳医院
深圳市南山区人民医院
南方科技大学医院
南方医科大学深圳医院
深圳市宝安区人民医院
深圳市宝安第二人民医院(集团)总医院
深圳市龙岗区第三人民医院
宝安中医院(集团)
深圳市中西医结合医院
深圳市宝安区中心医院
宝安纯中医治疗医院
深圳恒生医院
深圳万丰医院
深圳市第三人民医院
深圳市龙岗中心医院
深圳市龙岗区人民医院
龙岗区第二人民医院
深圳市龙岗区第四人民医院
深圳市龙岗区第五人民医院
深圳市龙岗区第六人民医院
北京中医药大学深圳医院
深圳市龙岗区耳鼻咽喉医院
深圳龙城医院
深圳华侨医院
深圳肖传国医院
深圳市人民医院龙华分院
深圳市龙华区人民医院
深圳市龙华区中心医院
深圳军龙医院
深圳市康宁医院(坪山院区)
深圳市坪山区人民医院
中山大学附属第七医院
中国科学院大学深圳医院(东院区)
深圳市大鹏新区葵涌人民医院
深圳市大鹏新区南澳人民医院
[15],[0],[0],[47.686190476190475],[24.46666666666666],[12.47047619047619],[84.62333333333333],[9.285714285714286],[93.90904761904761],[0.6857142857142857][18.0],[44.7],[0],[41.516666666666666],[19.816666666666666],[1],[46.95],[83.38333333333333],[1]
粤海街道
北京大学深圳医院
香港大学深圳医院
深圳市第二人民医院
深圳市中医院
中山大学附属第八医院
广州中医药大学深圳医院(福田)
深圳市福田区第二人民医院
深圳景田医院
深圳市人民医院
深圳市康宁医院(罗湖院区)
深圳市罗湖区人民医院
罗湖区中医院
深圳出入境边防检查总站医院
深圳市盐田区人民医院
深圳大学总医院
中国医学科学院阜外医院深圳医院
深圳市南山区人民医院
南方科技大学医院

In [39]:
stodabc(office,park)

龙岗创投大厦
福田红树林生态公园
皇岗公园
深圳中心公园
笔架山公园
荔枝公园
莲花山公园
彩田公园
梅林山公园
香蜜公园
翠竹公园
人民公园
深圳市儿童公园
深圳市围岭公园
东湖公园
洪湖公园
荔林公园
月亮湾公园
南山公园
荔香公园
大沙河公园
石鼓山公园
松坪山公园
文天祥纪念公园
四海公园
盐田中央公园
大梅沙海滨公园
翠岗公园
大王山公园
罗租岭公园
五指耙公园
平峦山公园
南昌公园
铁仔山公园
碧海湾公园
宝安公园
大钟山公园
黄金山公园
八仙岭公园
横岗人民公园
龙岗区大运公园
龙城公园
龙园公园
红花岭公园
凤凰山国家矿山公园
龙华公园
南园公园
坪山光祖公园
燕子岭生态公园
坪山公园
深圳市坪山区中心公园
光明开明公园
明湖城市公园
红花山公园
光明新城公园
翠湖公园
荔山公园
锣鼓山公园
禾塘山水公园
大鹏半岛国家地质公园
枫浪山公园
观音山公园
葵涌公园
罗田森林公园
大雁山公园
光明森林公园
松子坑森林公园
章阁城市公园
樟坑径城市公园
深圳湾公园
[38],[0],[0],[59.31505376344085],[26.23440860215053],[35.84946236559139],[121.3989247311828],[15.96774193548387],[137.3666666666667],[0.6451612903225806][4.0],[74.01666666666667],[0],[46.61666666666667],[4.0],[0],[56.61666666666667],[134.18333333333334],[1]
深圳国际文化大厦
福田红树林生态公园
皇岗公园
深圳中心公园
笔架山公园
荔枝公园
莲花山公园
彩田公园
梅林山公园
香蜜公园
翠竹公园
人民公园
深圳市儿童公园
深圳市围岭公园
东湖公园
洪湖公园
荔林公园
月亮湾公园
南山公园
荔香公园
大沙河公园
石鼓山公园
松坪山公园
文天祥纪念公园
四海公园
盐田中央公园
大梅沙海滨公园
翠岗公园
大王山公园
罗租岭公园
五指耙公园
平峦山公园
南昌公园
铁仔山公园
碧海湾公园
宝安公园
大钟山公园
黄金山公园
八仙岭公园
横岗人民公园
龙岗区大运公园
龙城公园
龙园公园
红花岭公园
凤凰山国家矿山公园
龙华公园
南园公园
坪山光祖公园
燕子岭生态

In [16]:
stodabc(factory,park)

华强创意产业园
福田红树林生态公园
皇岗公园
深圳中心公园
笔架山公园
荔枝公园
莲花山公园
彩田公园
梅林山公园
香蜜公园
翠竹公园
人民公园
深圳市儿童公园
深圳市围岭公园
东湖公园
洪湖公园
荔林公园
月亮湾公园
南山公园
荔香公园
大沙河公园
石鼓山公园
松坪山公园
文天祥纪念公园
四海公园
盐田中央公园
大梅沙海滨公园
翠岗公园
大王山公园
罗租岭公园
五指耙公园
平峦山公园
南昌公园
铁仔山公园
碧海湾公园
宝安公园
大钟山公园
黄金山公园
八仙岭公园
横岗人民公园
龙岗区大运公园
龙城公园
龙园公园
红花岭公园
凤凰山国家矿山公园
龙华公园
南园公园
坪山光祖公园
燕子岭生态公园
坪山公园
深圳市坪山区中心公园
光明开明公园
明湖城市公园
红花山公园
光明新城公园
翠湖公园
荔山公园
锣鼓山公园
禾塘山水公园
大鹏半岛国家地质公园
枫浪山公园
观音山公园
葵涌公园
罗田森林公园
大雁山公园
光明森林公园
松子坑森林公园
章阁城市公园
樟坑径城市公园
深圳湾公园
[24],[0],[0],[49.60407407407408],[23.854814814814816],[38.31888888888888],[111.77777777777781],[18.72222222222222],[130.50000000000003],[0.9777777777777777][5.0],[43.483333333333334],[0],[43.08333333333333],[8.0],[0],[49.06666666666667],[112.76666666666667],[1]
深圳市生物医药创新产业园
福田红树林生态公园
皇岗公园
深圳中心公园
笔架山公园
荔枝公园
莲花山公园
彩田公园
梅林山公园
香蜜公园
翠竹公园
人民公园
深圳市儿童公园
深圳市围岭公园
东湖公园
洪湖公园
荔林公园
月亮湾公园
南山公园
荔香公园
大沙河公园
石鼓山公园
松坪山公园
文天祥纪念公园
四海公园
盐田中央公园
大梅沙海滨公园
翠岗公园
大王山公园
罗租岭公园
五指耙公园
平峦山公园
南昌公园
铁仔山公园
碧海湾公园
宝安公园
大钟山公园
黄金山公园
八仙岭公园
横岗人民公园
龙岗区大运公园
龙城公园
龙园公园
红花岭公园
凤凰山国家矿山公园
龙华公园
南园公园
坪山光

In [18]:
stodabc(farm,park)

鹏飞路310号
福田红树林生态公园
皇岗公园
深圳中心公园
笔架山公园
荔枝公园
莲花山公园
彩田公园
梅林山公园
香蜜公园
翠竹公园
人民公园
深圳市儿童公园
深圳市围岭公园
东湖公园
洪湖公园
荔林公园
月亮湾公园
南山公园
荔香公园
大沙河公园
石鼓山公园
松坪山公园
文天祥纪念公园
四海公园
盐田中央公园
大梅沙海滨公园
翠岗公园
大王山公园
罗租岭公园
五指耙公园
平峦山公园
南昌公园
铁仔山公园
碧海湾公园
宝安公园
大钟山公园
黄金山公园
八仙岭公园
横岗人民公园
龙岗区大运公园
龙城公园
龙园公园
红花岭公园
凤凰山国家矿山公园
龙华公园
南园公园
坪山光祖公园
燕子岭生态公园
坪山公园
深圳市坪山区中心公园
光明开明公园
明湖城市公园
红花山公园
光明新城公园
翠湖公园
荔山公园
锣鼓山公园
禾塘山水公园
大鹏半岛国家地质公园
枫浪山公园
观音山公园
葵涌公园
罗田森林公园
大雁山公园
光明森林公园
松子坑森林公园
章阁城市公园
樟坑径城市公园
深圳湾公园
[33],[0],[0],[34.76342592592593],[33.21805555555556],[103.80138888888891],[171.78287037037032],[27.291666666666664],[199.074537037037],[0.25][4.0],[139.16666666666669],[0],[103.18333333333334],[7.0],[0],[37.0],[170.2],[0.0]
双晖现代农业
福田红树林生态公园
皇岗公园
深圳中心公园
笔架山公园
荔枝公园
莲花山公园
彩田公园
梅林山公园
香蜜公园
翠竹公园
人民公园
深圳市儿童公园
深圳市围岭公园
东湖公园
洪湖公园
荔林公园
月亮湾公园
南山公园
荔香公园
大沙河公园
石鼓山公园
松坪山公园
文天祥纪念公园
四海公园
盐田中央公园
大梅沙海滨公园
翠岗公园
大王山公园
罗租岭公园
五指耙公园
平峦山公园
南昌公园
铁仔山公园
碧海湾公园
宝安公园
大钟山公园
黄金山公园
八仙岭公园
横岗人民公园
龙岗区大运公园
龙城公园
龙园公园
红花岭公园
凤凰山国家矿山公园
龙华公园
南园公园
坪山光祖公园
燕子岭生态公园
坪山公园
深圳市坪山区中心公园
光明开明公园
明湖城市公园
红花

In [37]:
stodabc(resident_high,park)

沙河街道
福田红树林生态公园
皇岗公园
深圳中心公园
笔架山公园
荔枝公园
莲花山公园
彩田公园
梅林山公园
香蜜公园
翠竹公园
人民公园
深圳市儿童公园
深圳市围岭公园
东湖公园
洪湖公园
荔林公园
月亮湾公园
南山公园
荔香公园
大沙河公园
石鼓山公园
松坪山公园
文天祥纪念公园
四海公园
盐田中央公园
大梅沙海滨公园
翠岗公园
大王山公园
罗租岭公园
五指耙公园
平峦山公园
南昌公园
铁仔山公园
碧海湾公园
宝安公园
大钟山公园
黄金山公园
八仙岭公园
横岗人民公园
龙岗区大运公园
龙城公园
龙园公园
红花岭公园
凤凰山国家矿山公园
龙华公园
南园公园
坪山光祖公园
燕子岭生态公园
坪山公园
深圳市坪山区中心公园
光明开明公园
明湖城市公园
红花山公园
光明新城公园
翠湖公园
荔山公园
锣鼓山公园
禾塘山水公园
大鹏半岛国家地质公园
枫浪山公园
观音山公园
葵涌公园
罗田森林公园
大雁山公园
光明森林公园
松子坑森林公园
章阁城市公园
樟坑径城市公园
深圳湾公园
[24],[0],[0],[45.6774074074074],[25.34481481481481],[14.093703703703701],[85.11592592592594],[10.333333333333334],[95.44925925925925],[0.7111111111111111][3.0],[22.400000000000002],[0],[22.400000000000002],[3.0],[0],[44.0],[76.13333333333333],[1]
粤海街道
福田红树林生态公园
皇岗公园
深圳中心公园
笔架山公园
荔枝公园
莲花山公园
彩田公园
梅林山公园
香蜜公园
翠竹公园
人民公园
深圳市儿童公园
深圳市围岭公园
东湖公园
洪湖公园
荔林公园
月亮湾公园
南山公园
荔香公园
大沙河公园
石鼓山公园
松坪山公园
文天祥纪念公园
四海公园
盐田中央公园
大梅沙海滨公园
翠岗公园
大王山公园
罗租岭公园
五指耙公园
平峦山公园
南昌公园
铁仔山公园
碧海湾公园
宝安公园
大钟山公园
黄金山公园
八仙岭公园
横岗人民公园
龙岗区大运公园
龙城公园
龙园公园
红花岭公园
凤凰山国家矿山公园
龙华公园
南园公园
坪山光祖公园
燕子岭生态公园
坪山公园
深圳市坪山区中心公

In [36]:
stodabc(resident_medium,park)

凤凰街道
福田红树林生态公园
皇岗公园
深圳中心公园
笔架山公园
荔枝公园
莲花山公园
彩田公园
梅林山公园
香蜜公园
翠竹公园
人民公园
深圳市儿童公园
深圳市围岭公园
东湖公园
洪湖公园
荔林公园
月亮湾公园
南山公园
荔香公园
大沙河公园
石鼓山公园
松坪山公园
文天祥纪念公园
四海公园
盐田中央公园
大梅沙海滨公园
翠岗公园
大王山公园
罗租岭公园
五指耙公园
平峦山公园
南昌公园
铁仔山公园
碧海湾公园
宝安公园
大钟山公园
黄金山公园
八仙岭公园
横岗人民公园
龙岗区大运公园
龙城公园
龙园公园
红花岭公园
凤凰山国家矿山公园
龙华公园
南园公园
坪山光祖公园
燕子岭生态公园
坪山公园
深圳市坪山区中心公园
光明开明公园
明湖城市公园
红花山公园
光明新城公园
翠湖公园
荔山公园
锣鼓山公园
禾塘山水公园
大鹏半岛国家地质公园
枫浪山公园
观音山公园
葵涌公园
罗田森林公园
大雁山公园
光明森林公园
松子坑森林公园
章阁城市公园
樟坑径城市公园
深圳湾公园
[20],[0],[0],[51.039795918367346],[24.13877551020409],[17.882653061224488],[93.06122448979592],[15.510204081632653],[108.57142857142856],[0.9591836734693877][3.0],[28.516666666666666],[0],[28.516666666666666],[3.0],[0],[47.233333333333334],[83.11666666666666],[1]
玉塘街道
福田红树林生态公园
皇岗公园
深圳中心公园
笔架山公园
荔枝公园
莲花山公园
彩田公园
梅林山公园
香蜜公园
翠竹公园
人民公园
深圳市儿童公园
深圳市围岭公园
东湖公园
洪湖公园
荔林公园
月亮湾公园
南山公园
荔香公园
大沙河公园
石鼓山公园
松坪山公园
文天祥纪念公园
四海公园
盐田中央公园
大梅沙海滨公园
翠岗公园
大王山公园
罗租岭公园
五指耙公园
平峦山公园
南昌公园
铁仔山公园
碧海湾公园
宝安公园
大钟山公园
黄金山公园
八仙岭公园
横岗人民公园
龙岗区大运公园
龙城公园
龙园公园
红花岭公园
凤凰山国家矿山公园
龙华公园
南园公园
坪山光祖公园
燕子岭生态

In [37]:
stodabc(resident_low,park)

坪山街道
福田红树林生态公园
皇岗公园
深圳中心公园
笔架山公园
荔枝公园
莲花山公园
彩田公园
梅林山公园
香蜜公园
翠竹公园
人民公园
深圳市儿童公园
深圳市围岭公园
东湖公园
洪湖公园
荔林公园
月亮湾公园
南山公园
荔香公园
大沙河公园
石鼓山公园
松坪山公园
文天祥纪念公园
四海公园
盐田中央公园
大梅沙海滨公园
翠岗公园
大王山公园
罗租岭公园
五指耙公园
平峦山公园
南昌公园
铁仔山公园
碧海湾公园
宝安公园
大钟山公园
黄金山公园
八仙岭公园
横岗人民公园
龙岗区大运公园
龙城公园
龙园公园
红花岭公园
凤凰山国家矿山公园
龙华公园
南园公园
坪山光祖公园
燕子岭生态公园
坪山公园
深圳市坪山区中心公园
光明开明公园
明湖城市公园
红花山公园
光明新城公园
翠湖公园
荔山公园
锣鼓山公园
禾塘山水公园
大鹏半岛国家地质公园
枫浪山公园
观音山公园
葵涌公园
罗田森林公园
大雁山公园
光明森林公园
松子坑森林公园
章阁城市公园
樟坑径城市公园
深圳湾公园
[36],[0],[0],[66.76565656565656],[26.526767676767676],[39.0449494949495],[132.33737373737375],[18.636363636363637],[150.97373737373738],[1.0][17.0],[181.56666666666666],[0],[77.91666666666667],[28.0],[0],[65.76666666666667],[134.48333333333335],[1]
石井街道
福田红树林生态公园
皇岗公园
深圳中心公园
笔架山公园
荔枝公园
莲花山公园
彩田公园
梅林山公园
香蜜公园
翠竹公园
人民公园
深圳市儿童公园
深圳市围岭公园
东湖公园
洪湖公园
荔林公园
月亮湾公园
南山公园
荔香公园
大沙河公园
石鼓山公园
松坪山公园
文天祥纪念公园
四海公园
盐田中央公园
大梅沙海滨公园
翠岗公园
大王山公园
罗租岭公园
五指耙公园
平峦山公园
南昌公园
铁仔山公园
碧海湾公园
宝安公园
大钟山公园
黄金山公园
八仙岭公园
横岗人民公园
龙岗区大运公园
龙城公园
龙园公园
红花岭公园
凤凰山国家矿山公园
龙华公园
南园公园
坪山光祖公园
燕子岭生态公园
坪山公园
深圳市坪山区中